# DACON 4 COVID - 2차 제출 - Summary
## 제목 : COVID-19 Data EDA : 시각화로 한눈에 이해하는 COVID-19 (Update ver.2020-04-19)

### 코드설명 :

안녕하세요. 팀 쇠똥구리 입니다.

저희 팀의 1차 제출은 "COVID-19 data EDA : 시각화로 한눈에 이해하는 COVID-19"입니다. 

* EDA란? Exploratory Data Analysis의 줄임말로 탐색적 데이터 분석이라고 합니다. 데이터를 다양한 각도에서 관찰하고 이해하는 과정으로, 한마디로 데이터를 분석하기 전에 그래프나 통계적인 다양한 방법을 통해 자료를 직관적으로 이해하는 과정입니다.

본 대회의 목적인 COVID-19 확산 방지 및 예방을 위한 인사이트 발굴 이전에 EDA 과정이 우선되어야 할 텐데요, 

저희는 본격적인 분석 이전에, 데이터를 전체적으로 살펴보고 개별 값을 이해하며, 현상을 더 잘 바라볼 수 있도록 다양한 각도에서 살펴보는 과정을 선행하였습니다. 

EDA의 과정을 통해 필요한 데이터의 수집을 결정하고 미쳐 발견하진 못한 잠재적 패턴을 발굴하기도 합니다. (궁금하다면 3차 제출을 기대해주세요!)

특히 시각화는 데이터를 한눈에 이해하는데에 큰 도움이 됩니다.

저희의 첫 제출인 EDA는 주어진 개별 데이터들을 key 값의 내용에 따라 크게 3파트로 나누어 

1. Time Related, 2. Region Related, 3. Case + Patient Related 

로 나누어 분석을 진행해 보았습니다.

그럼 재미있게 보시고, 내용이 유익하셨다면 투표 부탁드립니다!

감사합니다.

* 링크 1 - 1. Time Related
* 링크 2 - 2. Region Related,
* 링크 3 - 3. Case + Patient Related 
* 링크 4 - EDA summary

---- 
# 0. Setting

필요한 모듈을 import한 후 dataset(Updated ver.2020.04.20)을 읽어들입니다.

In [2]:
import numpy as np 
import pandas as pd
import os
import glob
import re
import sys
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib import animation, rc
import geopandas as gpd
from shapely.geometry import Point, Polygon, LineString
import plotly.express as px
import folium
from folium import plugins
import branca
import json
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly
import plotly.io as pio
import matplotlib.pylab as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime, timedelta

pio.renderers.default = "notebook_connected"

In [3]:
files = glob.glob('dataset/*.csv')
data = []
for i in files :
    i = re.sub("dataset\\\\", "", i)
    data.append(re.sub(".csv","",i))
for i in range(len(files)) :
    globals()[data[i]] = pd.read_csv(files[i])
data

['Case',
 'PatientInfo',
 'PatientRoute',
 'Policy',
 'Region',
 'SearchTrend',
 'SeoulFloating',
 'Time',
 'TimeAge',
 'TimeGender',
 'TimeProvince',
 'Weather']

- - -

# 1. Time related

시간을 key 로 갖는 Dataset 들을 분석하였습니다. 시간에 따른 변화를 표현하기 위해 애니메이션 효과가 있는 plotly를 사용하였습니다. 재생 버튼과 축을 이용해서 살펴주시면 감사하겠습니다~!

### 1) Time

먼저 시간에 따른 누적 확진자와 사망자의 증가 추세를 살펴보았습니다. 

In [62]:
# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=Time.date , y=Time.confirmed, name="comfirmed"),
    secondary_y=False,
)

fig.add_trace(
    go.Scatter(x=Time.date, y=Time.deceased, name="deceased"),
    secondary_y=True,
)

# Add figure title
fig.update_layout(
    title_text="Confirmed & Deceased with Different Scale"
)

# Set x-axis title
fig.update_xaxes(title_text="Date")

# Set y-axes
fig.update_layout(
    yaxis=dict(
        title="Confirmed",
    ),
    yaxis2=dict(
        title="Deceased",
    )
)

fig.show()

확진자의 증가 폭이 2월 말에서 3월 초 폭발적으로 늘어난 점을 알 수 있습니다. 이에 비해 사망자의 증가는 꽤나 직선적인 형태를 띄고 있습니다.

### 2) TimeProvince

지역별 확진자의 증가추세를 애니메이션을 통해 살펴보았습니다.

In [63]:
fig = px.bar(TimeProvince, x="province", y="confirmed", color="province",
    animation_frame="date", animation_group="province", range_y=[0,5500])
fig.show()

뉴스에서 알 수 있었듯, 대구의 확진자가 2월 20일을 이후로 확진자가 가장 많았던 서울을 제치고 압도적으로 증가하는 것을 알 수 있습니다. 2월 말 경 확진자의 폭발적인 증가는 대구 지역에서 가장 많이 일어난 것으로 보여집니다. 

위의 확진자 수에 대한 애니메이션을 시계열 그래프로 나타내면 아래와 같습니다. 

다음으로는 지역별 사망자의 증가추세를 보여줍니다.

In [65]:
fig_dec = px.bar(TimeProvince, x="province", y="deceased", color="province",
    animation_frame="date", animation_group="province", range_y=[0,100])
fig_dec.show()

사망자의 수는 확진자의 수에 어느정도 시간의 간격을 두고 비례하는 비슷한 그래프 모양이 나오는 것을 확인할 수 있습니다. => 며칠 후에 ??

### 3) TimeAge

다음은 연령대에 대한 확진자 수의 증가를 애니메이션으로 나타낸 것입니다.

In [66]:
fig_age = px.bar(TimeAge, x="age", y="confirmed", color="age",
    animation_frame="date", animation_group="age", range_y=[0,3000])
fig_age.show()

다른 나이대에 비하여 20대 확진자 수가 가장 많았습니다.

### 4) TimeGender

시간에 따른 성별 확진자 수 증가를 애니메이션으로 나타내었습니다.

In [68]:
fig_sex = px.bar(TimeGender, x="sex", y="confirmed", color="sex",
    animation_frame="date", animation_group="sex", range_y=[0,6000])
fig_sex.show()

### 5) SeoulFloating

서울시의 유동인구 데이터를 시간의 흐름으로 살펴보았습니다.

데이터가 말이 안되는 관계로(2월 23일) 임의 수정하고 일별이 아닌 시간별로 시각화.

In [57]:
floatby = SFedit.groupby(['datehour','birth_year'],as_index = False).sum().pivot('datehour','birth_year').fp_num
fig1 = floatby.iplot(asFigure=True,kind='scatter')
fig1.show()

### 6) SearchTrend

시간에 따른 네 가지 키워드의 검색량을 표현해 보았습니다.

In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(
                x=SearchTrend.date,
                y=SearchTrend.cold,
                name="Cold",
                line_color='brown',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=SearchTrend.date,
                y=SearchTrend.flu,
                name="Flu",
                line_color='skyblue',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=SearchTrend.date,
                y=SearchTrend.pneumonia,
                name="Pneumonia",
                line_color='green',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=SearchTrend.date,
                y=SearchTrend.coronavirus,
                name="Corona",
                line_color='red',
                opacity=0.8))

# Use date string to set xaxis range
fig.update_layout(title_text="Search Trend")
fig.show()

COVID 19 가 등장한 기간 동안의 검색량을 보면 아래와 같습니다.

In [71]:
fig = go.Figure()

df = SearchTrend.iloc[SearchTrend[SearchTrend.date == "2019-12-19"].index[0]:]

fig.add_trace(go.Scatter(
                x=df.date,
                y=df.cold,
                name="Cold",
                line_color='brown',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=df.date,
                y=df.flu,
                name="Flu",
                line_color='skyblue',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=df.date,
                y=df.pneumonia,
                name="Pneumonia",
                line_color='green',
                opacity=0.8))

fig.add_trace(go.Scatter(
                x=df.date,
                y=df.coronavirus,
                name="Corona",
                line_color='red',
                opacity=0.8))

# Use date string to set xaxis range
fig.update_layout(title_text="Search Trend Recent")
fig.show()

### 6-1) Search Trend + Confirmed

Search Trend 를 Confirmed 수와 함께 보았습니다. 아래 그래프는 위 그래프에서 잘 보이지 않던 Pneumonia 와 Flu 의 트렌드를 더 쉽게 보기 위해 스케일링 되어 있습니다.

In [72]:
grouped = (Time.groupby(['date'])
            .agg({'confirmed':'sum', 'deceased':'sum'})
            .reset_index())
merged = pd.merge(grouped,SearchTrend,
        how='left',
        on=('date')
        )

In [73]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=merged.date , y=merged.confirmed, name="Comfirmed"), secondary_y=False)

fig.add_trace(
    go.Scatter(x=merged.date, y=merged.cold, name="Cold trend"), secondary_y=True)

fig.add_trace(
    go.Scatter(x=merged.date, y=merged.flu, name="Flu trend"), secondary_y=True)

fig.add_trace(
    go.Scatter(x=merged.date, y=merged.pneumonia, name="Pneumonia trend"), secondary_y=True)

# Add figure title
fig.update_layout(
    title_text="Confirmed & Search Trend")

# Set x-axis title
fig.update_xaxes(title_text="Date")

# Set y-axes
fig.update_layout(
    yaxis=dict(title="Confirmed"),
    yaxis2=dict(title="Trend")
)

fig.show()

확진자 수가 증가하고, 사람들이 COVID-19 에 대하여 알게 되기 시작하면서 폐렴의 검색량이 줄게 되었음을 볼 수 있습니다. => 대신 어떤 검색량이 또 늘었는가??????????????

- - -

# 2. Region related

### 1) Region

Region 데이터셋은 크게 Count 와 Ratio 관련 변수로 나누어 살펴보겠습니다.

### 1-1) Count

In [81]:
grouped = (Region[Region.province != "Korea"].groupby(['province'])
            .agg({'elementary_school_count':'sum', 'kindergarten_count':'sum', 'university_count':'sum', 'nursing_home_count':'sum'})
            .reset_index())
    
grouped.iloc[:,1:len(grouped)] = grouped.iloc[:,1:len(grouped)]/2 # Region province별 첫 행이 전체 sum값이 들어있음

import plotly.graph_objects as go
from plotly.subplots import make_subplots

labels = grouped.province

# Pie Chart !
fig = make_subplots(rows=2, cols=2, specs=[[{'type':'domain'}, {'type':'domain'}], [{'type':'domain'}, {'type':'domain'}]]
                    ,subplot_titles=["kindergarten", "Elementary", "University", "Nursing Home"])
fig.add_trace(go.Pie(labels=labels, values=grouped.kindergarten_count, name="kindergarten count"),
              1, 1)
fig.add_trace(go.Pie(labels=labels, values=grouped.elementary_school_count, name="Elementary School count"),
              1, 2)
fig.add_trace(go.Pie(labels=labels, values=grouped.university_count, name="University count"),
              2, 1)
fig.add_trace(go.Pie(labels=labels, values=grouped.nursing_home_count, name="Nursing Home count"),
              2, 2)

fig.update_traces(hole=.4, hoverinfo="label+percent+name")

fig.update_layout(
    title_text="Region Information")
fig.show()

수도권 지역에 관련 시설들이 많이 분포되어있습니다. 특히 서울에는 요양원이 상대적으로 많으며, 경기도에는 유치원이 상대적으로 많습니다. 

### 2) PatientInfo : 지역별 확진자수

- - -

# 3. Case + Patient Related

### 1) Patient : 확진자 경로

주어진 PatientRoute 데이터를 가지고 확진자의 경로를 보기 쉽게 지도 위에 애니메이션으로 나타냈습니다.

#### 경로의 색깔 : 확진자가 접촉한 사람 수에 따라서

#### 접촉자 0 명 : 초록색

#### 접촉자 1~10 명 : 파란색

#### 접촉자 11~100명 : 노란색

#### 접촉자 100 초과 : 빨간색

#### 접촉자 수가 최다인 사람 : 검정색

In [6]:
contnum = PatientInfo.iloc[:,[0,12]]
clr = []
for i in range(len(contnum)) :
    if contnum.contact_number[i] == 0 :
        clr.append("green")
    elif contnum.contact_number[i] <= 10 :
        clr.append("blue")
    elif contnum.contact_number[i] <= 100 :
        clr.append("yellow")
    elif contnum.contact_number[i] == max(contnum.contact_number) :
        clr.append("black")
    else : 
        clr.append("red")
contnum["color"] = clr
wcontnum = pd.merge(PatientRoute,contnum,
        how ='left',
        on = 'patient_id').fillna(0)
route_geo = gpd.GeoDataFrame(wcontnum,geometry=gpd.points_from_xy(PatientRoute.longitude,PatientRoute.latitude))

linerange = route_geo[route_geo['patient_id'] == route_geo['patient_id'].shift(1)].index
linerange = linerange.drop(linerange[-1])
lines = [ {
                "coordinates": [
                 [route_geo["longitude"][i] , route_geo["latitude"][i] ],
                 [route_geo["longitude"][i+1] , route_geo["latitude"][i+1],]
                   ],
                "dates": [
                 route_geo["date"][i],
                 route_geo["date"][i+1]
                   ],
                "color": route_geo["color"][i]
                     } for i in linerange ] 
features = [
     {
         'type': 'Feature',
         'geometry': {
            'type': 'LineString',
            'coordinates': line['coordinates'],
                },
         'properties': {
            'times': line['dates'],
            'style': {
                'color' : line['color']
            },
            'icon' : 'circle',
            'iconstyle':{
                    'fillOpacity': 0.8,
                    'stroke': 'true',
                    'radius': 3
                }
                }
        }
        for line in lines
    ]


m = folium.Map(
  location=[36.5053542,127.7043419],
  zoom_start=8
)
plugins.TimestampedGeoJson({
    'type': 'FeatureCollection',
    'features': features,
}, period='PT6H', add_last_point=True).add_to(m)
m.save('with_color.html')
m

### 2) 시간에 따른 infection case 별 확진자 수

In [90]:
inf_case = PatientInfo.infection_case.unique()
for i in range(len(inf_case)) :
    globals()['case'+ str(i)] = PatientInfo[PatientInfo.infection_case == inf_case[i]]
    globals()['case'+str(i)] = pd.DataFrame(globals()['case'+ str(i)].groupby('confirmed_date').count().cumsum().patient_id).reset_index()
    globals()['case'+str(i)].columns = ['confirmed_date','case'+str(i)]   

merged = case0
for i in [x for x in range(len(inf_case)) if x != 0] :
    merged = pd.merge(merged , globals()['case'+str(i)],how= 'outer',on='confirmed_date')
merged = merged.sort_values(by = 'confirmed_date').reset_index()
merged = merged.drop('index',axis=1)
merged.columns = np.insert(inf_case,0,'confirmed_date')
merged = merged.fillna(method='pad')
merged = merged.fillna(0)
merged = merged.set_index('confirmed_date')
fig = merged.iplot(asFigure=True, kind='scatter')
fig.show()

확진 원인으로는 접촉에 의한 감염이 가장 많았으며, 해외 확진자의 유입이 3월 중순부터 가파르게 상승하고 있습니다.

----
이상 주어진 dataset을 통한 EDA를 마치겠습니다!

다음번에는 이번 EDA를 가지고 외부 데이터를 활용하여 발전시킨 재미있는 분석을 업데이트 하겠습니다.

감사합니다!